## Alpha Compositor Demo
This notebook shows how to run all pods, inspect saved diagnostics, and preview alpha outputs.


In [1]:
import sys, pathlib, pandas as pd
from pprint import pprint

repo_root = pathlib.Path('..').resolve()
if str(repo_root) not in sys.path:
    sys.path.insert(0, str(repo_root))

from alpha_compositor.pipeline import run_pod_grid
from alpha_compositor.data_loader import load_config


In [2]:
# Load config
cfg_path = '../config/config.json'
cfg = load_config(cfg_path)
print(cfg_path)
pprint({k: v for k, v in cfg.items() if k in ['price_file','factor_dir','output_dir']})


../config/config.json
{'factor_dir': '../data/factors',
 'output_dir': '../../data/alpha',
 'price_file': '../data/data-processed/price_daily.parquet'}


In [3]:
# Run all pods defined in config (includes ML-only global_ml)
pod_results = run_pod_grid(cfg_path)
for pod, res in pod_results.items():
    for method, r in res.items():
        print(pod, method, 'IC:', r['metrics'].get('ic'), 'path:', r.get('alpha_path'))


/Users/edl/miniforge3/envs/quantlab/lib/python3.11/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: divide by zero encountered in matmul
  ret = a @ b
/Users/edl/miniforge3/envs/quantlab/lib/python3.11/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: overflow encountered in matmul
  ret = a @ b
/Users/edl/miniforge3/envs/quantlab/lib/python3.11/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: invalid value encountered in matmul
  ret = a @ b
/Users/edl/miniforge3/envs/quantlab/lib/python3.11/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: divide by zero encountered in matmul
  ret = a @ b
/Users/edl/miniforge3/envs/quantlab/lib/python3.11/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: overflow encountered in matmul
  ret = a @ b
/Users/edl/miniforge3/envs/quantlab/lib/python3.11/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: invalid value encountered in matmul
  ret = a @ b
/Users/edl/miniforge3/envs/quantlab/lib/py

core_systematic equal IC: 0.006918286067607038 path: ../../data/alpha/alpha_core_systematic_equal.parquet
core_systematic ic_weight IC: 0.009968107609062879 path: ../../data/alpha/alpha_core_systematic_ic_weight.parquet
core_systematic mlr IC: 0.00634607332876927 path: ../../data/alpha/alpha_core_systematic_mlr.parquet
core_systematic bayesian IC: 0.009608938887189713 path: ../../data/alpha/alpha_core_systematic_bayesian.parquet
core_systematic gmv IC: 0.007632183668214804 path: ../../data/alpha/alpha_core_systematic_gmv.parquet
core_systematic mvo IC: 0.009578729302794568 path: ../../data/alpha/alpha_core_systematic_mvo.parquet
event_info equal IC: 0.00954027338409947 path: ../../data/alpha/alpha_event_info_equal.parquet
event_info ic_weight IC: 0.011659376245315498 path: ../../data/alpha/alpha_event_info_ic_weight.parquet
event_info mlr IC: 0.00652822543083482 path: ../../data/alpha/alpha_event_info_mlr.parquet
event_info bayesian IC: 0.009625773160716184 path: ../../data/alpha/alpha

In [4]:
# Inspect aggregated diagnostics saved during run_pod_grid
import pandas as pd
metrics_path = pathlib.Path(repo_root / 'diagnostics/alpha_metrics_all.csv')
if metrics_path.exists():
    diag = pd.read_csv(metrics_path)
    display(diag.head())
else:
    print('Diagnostics file not found:', metrics_path)


pod     method        ic        ir  turnover   decay_5  \
0  core_systematic      equal  0.006918  0.087150  0.010355  0.005876   
1  core_systematic  ic_weight  0.009968  0.087341  0.016211  0.008811   
2  core_systematic        mlr  0.006346  0.062333  0.021423  0.006674   
3  core_systematic   bayesian  0.009609  0.099687  0.017468  0.008733   
4  core_systematic        gmv  0.007632  0.082609  0.012866  0.006667   

   decay_10  decay_21                                         alpha_path  
0  0.005448  0.004193  ../../data/alpha/alpha_core_systematic_equal.p...  
1  0.008736  0.007290  ../../data/alpha/alpha_core_systematic_ic_weig...  
2  0.005739  0.005254  ../../data/alpha/alpha_core_systematic_mlr.par...  
3  0.008093  0.006649  ../../data/alpha/alpha_core_systematic_bayesia...  
4  0.006216  0.005284  ../../data/alpha/alpha_core_systematic_gmv.par...

In [5]:
# Preview one of the saved alpha series
alpha_dir = pathlib.Path(cfg['output_dir']).resolve()
print('Alpha dir:', alpha_dir)
if alpha_dir.exists():
    files = sorted(alpha_dir.glob('alpha_*.parquet'))
    if files:
        sample = files[0]
        print('Loading sample alpha:', sample.name)
        alpha_df = pd.read_parquet(sample)
        display(alpha_df.head())
    else:
        print('No alpha files found in', alpha_dir)
else:
    print('Alpha dir missing')


Alpha dir: /Users/edl/Documents/dev/quantlab_v2/data/alpha
Loading sample alpha: alpha_core_systematic_bayesian.parquet


date ticker     alpha
0 2005-10-04      A  0.100925
1 2005-10-04     AA  0.023075
2 2005-10-04    AAL -0.389138
3 2005-10-04    AAP  0.196078
4 2005-10-04   AAPL  0.523601